Gather some statistics about the datasets, vocabularies and codelists loaded into PMD.

In [1]:
from SPARQLWrapper import SPARQLWrapper2
import pandas as pd
from IPython.display import HTML

endpoint = "https://production-drafter-ons-alpha.publishmydata.com/v1/sparql/live"
sparql = SPARQLWrapper2(endpoint)

Find the distinct datasets

In [2]:
sparql.setQuery("""
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX qb:   <http://purl.org/linked-data/cube#>
PREFIX pmd:  <http://publishmydata.com/def/dataset#>
PREFIX gdp:  <http://gss-data.org.uk/def/gdp#>

SELECT DISTINCT ?dataset ?datasetLabel ?graph ?family
WHERE {
  ?dataset a qb:DataSet ;
         rdfs:label ?datasetLabel ;
         pmd:graph ?graph .
  OPTIONAL {
    ?dataset gdp:family [rdfs:label ?family]
  }
}
""")

results = sparql.query().bindings

table = pd.DataFrame()
table['Label'] = pd.Series({
    res['dataset'].value: res['datasetLabel'].value
    for res in results
})

table['Graph'] = pd.Series({
    res['dataset'].value: res['graph'].value
    for res in results
})

table['Family'] = pd.Series({
    res['dataset'].value: res['family'].value if 'family' in res else 'Trade'
    for res in results
})
table

Label  \
http://gss-data.org.uk/data/ons-pink-book-chapt...                            ONS Pink Book Chapter 3   
http://gss-data.org.uk/data/ons-bop-individual-...                    ONS BoP Individual Country Data   
http://gss-data.org.uk/data/gss_data/migration/...                      Mid-Year Population Estimates   
http://gss-data.org.uk/data/gss_data/migration/...            Migration between Scotland and Overseas   
http://gss-data.org.uk/data/gss_data/migration/...  National Insurance number allocations to adult...   
http://gss-data.org.uk/data/gss_data/migration/...                Local area migration indicators, UK   
http://gss-data.org.uk/data/gss_data/migration/...  Long-term international migration 2.07, age an...   
http://gss-data.org.uk/data/gss_data/migration/...  Long-term international migration 2.06, area o...   
http://gss-data.org.uk/data/gss_data/migration/...  Long-term international migration 2.01a, citiz...   
http://gss-data.org.uk/data/gss_data/migration/...  Long-term international migration 2.02, countr...   
http://gss-data.org.uk/data/gss_data/migration/...  Long-term international migration 2.05, usual ...   
http://gss-data.org.uk/data/gss_data/migration/...  Long-term international migration 2.04, main r...   
http://gss-data.org.uk/data/gss_data/migration/...  International Passenger Survey 4.02, main reas...   
http://gss-data.org.uk/data/gss_data/migration/...  International Passenger Survey 4.04, area of d...   
http://gss-data.org.uk/data/gss_data/migration/...  International Passenger Survey 4.01, citizensh...   
http://gss-data.org.uk/data/gss_data/migration/...  Immigration statistics, October to December 20...   
http://gss-data.org.uk/data/gss_data/health/hmr...                                       Alcohol Duty   
http://gss-data.org.uk/data/gss_data/health/doh...  Census of drug and alcohol treatment services ...   
http://gss-data.org.uk/data/gss_data/trade/ons_bop                                Balance of payments   
http://gss-data.org.uk/data/gss_data/health/ons...                  Alcohol-specific deaths in the UK   
http://gss-data.org.uk/data/gss_data/trade/hmrc...  UK Trade in Goods by Business Characteristics ...   
http://gss-data.org.uk/data/gss_data/trade/ons-...  Trade in goods: country-by-commodity imports a...   
http://gss-data.org.uk/data/gss_data/trade/ons-...  UK trade in services: service type by partner ...   
http://gss-data.org.uk/data/gss_data/trade/ons_...                               UK trade time series   
http://gss-data.org.uk/data/gss_data/trade/ons_abs     Annual Business Survey importers and exporters   
http://gss-data.org.uk/data/gss_data/trade/ons-fdi   Foreign direct investment involving UK companies   
http://gss-data.org.uk/data/gss_data/trade/ons-...                    International trade in services   
http://gss-data.org.uk/data/gss_data/trade/hmrc...                  UK Regional Trade Statistics (RTS   
http://gss-data.org.uk/data/gss_data/trade/ons_cpa  UK trade in goods by classification of product...   
http://gss-data.org.uk/data/gss_data/trade/ons-...       Regionalised estimates of UK service exports   
...                                                                                               ...   
http://gss-data.org.uk/data/gss_data/disability...  Co-occurring substance misuse and mental healt...   
http://gss-data.org.uk/data/gss_data/disability...  Co-occurring substance misuse and mental healt...   
http://gss-data.org.uk/data/gss_data/disability...  Co-occurring substance misuse and mental healt...   
http://gss-data.org.uk/data/gss_data/disability...  Co-occurring substance misuse and mental healt...   
http://gss-data.org.uk/data/gss_data/disability...  Co-occurring substance misuse and mental healt...   
http://gss-data.org.uk/data/gss_data/disability...  Co-occurring substance misuse and mental healt...   
http://gss-data.org.uk/data/gss_data/disability...  Co-occurring substance misuse and mental healt...   
h

Find the sizes of the graphs.

In [3]:
sparql.setQuery("""
SELECT (COUNT(*) as ?size) ?graph
WHERE {
  GRAPH ?graph {
    ?s ?p ?o
  }
} GROUP BY ?graph
""")

sizes = pd.DataFrame()
sizes['Triples'] = pd.Series({
    res['graph'].value : int(res['size'].value)
    for res in sparql.query().bindings
})
sizes

Triples
http://purl.org/dc/terms/                               866
http://gss-data.org.uk/graph/semstats/cpav2008-...    28071
http://gss-data.org.uk/graph/semstats/cpav2008        47707
http://gss-data.org.uk/graph/semstats/cpav21          44275
http://gss-data.org.uk/graph/semstats/cpcv11          29269
http://gss-data.org.uk/graph/semstats/cpcv2           44159
http://gss-data.org.uk/graph/semstats/cpcv21          36837
http://gss-data.org.uk/graph/semstats/cpcv11-cpcv2    15202
http://gss-data.org.uk/graph/semstats/cpcv2-cpcv21    14788
http://gss-data.org.uk/graph/semstats/isicr31          5438
http://gss-data.org.uk/graph/semstats/isicr31-c...    13350
http://gss-data.org.uk/graph/semstats/isicr31-i...     4116
http://gss-data.org.uk/graph/semstats/isicr4           9249
http://gss-data.org.uk/graph/semstats/isicr4-cp...    13320
http://gss-data.org.uk/graph/semstats/isicr4-cpcv2    12305
http://gss-data.org.uk/graph/semstats/isicr4-na...     4311
http://gss-data.org.uk/graph/semstats/isicr4-na...     7591
http://gss-data.org.uk/graph/semstats/nacer11          9605
http://gss-data.org.uk/graph/semstats/nacer2          12806
http://gss-data.org.uk/graph/semstats/nacer2-cp...    16066
http://gss-data.org.uk/graph/semstats/nacer2-cp...    15716
http://gss-data.org.uk/graph/semstats/nacer11-n...     5096
http://gss-data.org.uk/graph/semstats/naics2012       17756
http://xmlns.com/foaf/0.1/                              631
http://publishmydata.com/graph/vocabulary/22-rd...      102
http://publishmydata.com/graph/vocabulary/admingeo     3369
http://publishmydata.com/graph/vocabulary/sdmx          120
http://publishmydata.com/graph/vocabulary/skos          273
http://publishmydata.com/graph/vocabulary/sdmx-...      295
http://publishmydata.com/graph/vocabulary/stati...       32
...                                                     ...
http://gss-data.org.uk/graph/gss_data/disabilit...       16
http://gss-data.org.uk/graph/gss_data/disabilit...     8964
http://gss-data.org.uk/graph/gss_data/disabilit...       16
http://gss-data.org.uk/graph/gss_data/disabilit...    17376
http://gss-data.org.uk/graph/gss_data/disabilit...       16
http://gss-data.org.uk/graph/gss_data/disabilit...    38862
http://gss-data.org.uk/graph/gss_data/disabilit...       16
http://gss-data.org.uk/graph/gss_data/disabilit...     2059
http://gss-data.org.uk/graph/gss_data/disabilit...       16
http://gss-data.org.uk/graph/gss_data/disabilit...     2783
http://gss-data.org.uk/graph/gss_data/disabilit...       16
http://gss-data.org.uk/graph/gss_data/disabilit...    11199
http://gss-data.org.uk/graph/gss_data/disabilit...       16
http://gss-data.org.uk/graph/gss_data/disabilit...    28329
http://gss-data.org.uk/graph/gss_data/disabilit...       16
http://gss-data.org.uk/graph/gss_data/disabilit...      810
http://gss-data.org.uk/graph/gss_data/disabilit...       16
http://gss-data.org.uk/graph/gss_data/disabilit...      270
http://gss-data.org.uk/graph/gss_data/disabilit...       16
http://gss-data.org.uk/graph/gss_data/disabilit...      862
http://gss-data.org.uk/graph/gss_data/disabilit...       16
http://gss-data.org.uk/graph/gss_data/disabilit...      810
http://gss-data.org.uk/graph/gss_data/disabilit...       16
http://gss-data.org.uk/graph/gss_data/disabilit...      113
http://gss-data.org.uk/graph/gss_data/disabilit...       16
http://gss-data.org.uk/graph/gss_data/disabilit...    62889
http://gss-data.org.uk/graph/gss_data/disabilit...   775784
http://gss-data.org.uk/graph/gss_data/disabilit...        2
http://gss-data.org.uk/graph/dwp-frs-people              27
http://gss-data.org.uk/graph/phe-group                   51

[540 rows x 1 columns]

In [4]:
table = table.merge(sizes, left_on='Graph', right_index=True)
table.drop(columns=['Graph'], inplace=True)
table

Label  \
http://gss-data.org.uk/data/ons-pink-book-chapt...                            ONS Pink Book Chapter 3   
http://gss-data.org.uk/data/ons-bop-individual-...                    ONS BoP Individual Country Data   
http://gss-data.org.uk/data/gss_data/migration/...                      Mid-Year Population Estimates   
http://gss-data.org.uk/data/gss_data/migration/...            Migration between Scotland and Overseas   
http://gss-data.org.uk/data/gss_data/migration/...  National Insurance number allocations to adult...   
http://gss-data.org.uk/data/gss_data/migration/...                Local area migration indicators, UK   
http://gss-data.org.uk/data/gss_data/migration/...  Long-term international migration 2.07, age an...   
http://gss-data.org.uk/data/gss_data/migration/...  Long-term international migration 2.06, area o...   
http://gss-data.org.uk/data/gss_data/migration/...  Long-term international migration 2.01a, citiz...   
http://gss-data.org.uk/data/gss_data/migration/...  Long-term international migration 2.02, countr...   
http://gss-data.org.uk/data/gss_data/migration/...  Long-term international migration 2.05, usual ...   
http://gss-data.org.uk/data/gss_data/migration/...  Long-term international migration 2.04, main r...   
http://gss-data.org.uk/data/gss_data/migration/...  International Passenger Survey 4.02, main reas...   
http://gss-data.org.uk/data/gss_data/migration/...  International Passenger Survey 4.04, area of d...   
http://gss-data.org.uk/data/gss_data/migration/...  International Passenger Survey 4.01, citizensh...   
http://gss-data.org.uk/data/gss_data/migration/...  Immigration statistics, October to December 20...   
http://gss-data.org.uk/data/gss_data/health/hmr...                                       Alcohol Duty   
http://gss-data.org.uk/data/gss_data/health/doh...  Census of drug and alcohol treatment services ...   
http://gss-data.org.uk/data/gss_data/trade/ons_bop                                Balance of payments   
http://gss-data.org.uk/data/gss_data/health/ons...                  Alcohol-specific deaths in the UK   
http://gss-data.org.uk/data/gss_data/trade/hmrc...  UK Trade in Goods by Business Characteristics ...   
http://gss-data.org.uk/data/gss_data/trade/ons-...  Trade in goods: country-by-commodity imports a...   
http://gss-data.org.uk/data/gss_data/trade/ons-...  UK trade in services: service type by partner ...   
http://gss-data.org.uk/data/gss_data/trade/ons_...                               UK trade time series   
http://gss-data.org.uk/data/gss_data/trade/ons_abs     Annual Business Survey importers and exporters   
http://gss-data.org.uk/data/gss_data/trade/ons-fdi   Foreign direct investment involving UK companies   
http://gss-data.org.uk/data/gss_data/trade/ons-...                    International trade in services   
http://gss-data.org.uk/data/gss_data/trade/hmrc...                  UK Regional Trade Statistics (RTS   
http://gss-data.org.uk/data/gss_data/trade/ons_cpa  UK trade in goods by classification of product...   
http://gss-data.org.uk/data/gss_data/trade/ons-...       Regionalised estimates of UK service exports   
...                                                                                               ...   
http://gss-data.org.uk/data/gss_data/housing/sc...                  Empty properties and second homes   
http://gss-data.org.uk/data/gss_data/trade/ons-...  UK trade in goods by industry, country and com...   
http://gss-data.org.uk/data/gss_data/housing/wg...                           Social housing vacancies   
http://gss-data.org.uk/data/gss_data/health/nis...                  Alcohol-Specific Deaths 2007-2017   
http://gss-data.org.uk/data/gss_data/housing/wg...                              Council tax dwellings   
http://gss-data.org.uk/data/gss_data/trade/ons-...  UK total trade: all countries, non-seasonally ...   
http://gss-data.org.uk/data/gss_data/disability...    Family Resources Survey: financial year 2017/18   
h

In [5]:
from urllib.parse import urlencode
def gss_url(uri):
    return 'http://gss-data.org.uk/resource?' + urlencode({
        'uri': uri
    })

table['Dataset'] = table.apply(lambda x: f'<a href="{gss_url(x.name)}">{x.Label}</a>', axis=1)
table.drop(columns=['Label'], inplace=True)
table = table[['Dataset', 'Family', 'Triples']]
table = table.sort_values(by=['Family', 'Dataset'])
table = table.set_index(['Family', 'Dataset'])
pd.set_option('max_colwidth', -1)
with open('dataset-stats.html', 'w') as f:
    f.write(table.to_html(escape=False, index=True))
HTML(table.to_html(escape=False, index=True))